# This notebook is a package of "Greedy Forward Selection"

In [0]:
# -*- coding: utf-8 -*-

## Abstract of this package heavy version in Japanese  
本手法は特徴量の組み合わせを変えてモデル(xgboost)に学習させることを繰り返し、その精度をもとに重要な変数を探索していきます。手順は以下。  
1. 使用する特徴量の集合を空から始める（この集合をMとする）  
2. 候補となる特徴量のそれぞれについてMに加えた場合のベストスコアを計算する（このときハイパーパラメータのチューニングもする）  
3. 最もスコアが改善した特徴量をMに加える
4. ３に採用された特徴量を候補から外し、2.3.をスコアの改善が止まるまで繰り返す  

## Data Preparation

In [1]:
import numpy as np
import pandas as pd

train = pd.read_csv('sample_data/train_preprocessed.csv')
train_x = train.drop(['target'], axis=1)
train_y = train['target']
test_x = pd.read_csv('sample_data/test_preprocessed.csv')

In [2]:
train.head()

age  sex      height     weight  product   amount  medical_info_a1  \
0   50    1  166.445608  65.016732        9  7000000              134   
1   68    0  164.334615  56.544217        0  7000000              438   
2   77    1  167.462917  54.242267        2  6000000              313   
3   17    1  177.097725  71.147762        3  8000000              342   
4   62    0  158.165788  65.240697        1  9000000              327   

   medical_info_a2  medical_info_a3  medical_info_b1  ...  medical_keyword_6  \
0              202                1               11  ...                  1   
1              263                3               14  ...                  0   
2              325                1               18  ...                  1   
3              213                2               11  ...                  0   
4              102                0               14  ...                  0   

   medical_keyword_7  medical_keyword_8  medical_keyword_9  \
0                  0                  1                  0   
1                  1                  1                  0   
2                  0                  1                  0   
3                  0                  1                  0   
4                  1                  1                  1   

   medical_keyword_10  year  month  day  yearmonth  target  
0                   0  2015      2    3      24182       0  
1                   0  2015      5    9      24185       0  
2                   0  2016      2   13      24194       1  
3                   0  2015      7    6      24187       0  
4                   0  2016      9   17      24201       1  

[5 rows x 29 columns]

In [7]:
train.shape, test_x.shape

((10000, 29), (10000, 28))

In [3]:
# devide dataset to training and validarion
from sklearn.model_selection import KFold

kf = KFold(n_splits=4, shuffle=True, random_state=71)
tr_idx, va_idx = list(kf.split(train_x))[0]
tr_x, va_x = train_x.iloc[tr_idx], train_x.iloc[va_idx]
tr_y, va_y = train_y.iloc[tr_idx], train_y.iloc[va_idx]

In [13]:
#Check features
features = train_x.columns
print(features)

Index(['age', 'sex', 'height', 'weight', 'product', 'amount',
       'medical_info_a1', 'medical_info_a2', 'medical_info_a3',
       'medical_info_b1', 'medical_info_b2', 'medical_info_b3',
       'medical_info_c1', 'medical_info_c2', 'medical_keyword_1',
       'medical_keyword_2', 'medical_keyword_3', 'medical_keyword_4',
       'medical_keyword_5', 'medical_keyword_6', 'medical_keyword_7',
       'medical_keyword_8', 'medical_keyword_9', 'medical_keyword_10', 'year',
       'month', 'day', 'yearmonth'],
      dtype='object')


## Check features (just little)

In [33]:
import pandas_profiling as pdp
pdp.ProfileReport(train_x)

In [36]:
train.corr()

age       sex    height    weight   product  \
age                 1.000000 -0.012421 -0.021233 -0.007697  0.006160   
sex                -0.012421  1.000000  0.514861  0.326875 -0.023463   
height             -0.021233  0.514861  1.000000  0.626530 -0.004351   
weight             -0.007697  0.326875  0.626530  1.000000  0.011383   
product             0.006160 -0.023463 -0.004351  0.011383  1.000000   
amount             -0.002223  0.012535 -0.010462 -0.015761 -0.475003   
medical_info_a1    -0.003493  0.005949  0.002690  0.001887  0.007287   
medical_info_a2     0.006303  0.000446  0.005158  0.026011  0.002404   
medical_info_a3     0.015710  0.022126  0.020852  0.005449  0.008296   
medical_info_b1     0.008479  0.002288  0.000430 -0.019404  0.011022   
medical_info_b2     0.011212  0.008896 -0.001417 -0.008451 -0.005305   
medical_info_b3     0.007309 -0.009409 -0.005266 -0.011740 -0.010468   
medical_info_c1    -0.005011  0.005622  0.041641  0.026505 -0.011584   
medical_info_c2    -0.042582 -0.013959 -0.005904  0.000204 -0.005540   
medical_keyword_1  -0.002322 -0.002076  0.012681  0.016197  0.005811   
medical_keyword_2   0.009923 -0.008907 -0.011517 -0.010971  0.013045   
medical_keyword_3   0.000083 -0.004301  0.004488  0.002790 -0.009903   
medical_keyword_4  -0.002916  0.002695 -0.009734  0.001686  0.002277   
medical_keyword_5   0.001144 -0.012001 -0.012961 -0.015356 -0.003412   
medical_keyword_6   0.002183 -0.008745 -0.018654 -0.007124 -0.008521   
medical_keyword_7   0.000756  0.019544  0.009393 -0.001829 -0.006754   
medical_keyword_8   0.007739 -0.006820  0.000329 -0.000139  0.004316   
medical_keyword_9   0.004909 -0.001773 -0.007587 -0.002658  0.002608   
medical_keyword_10 -0.005275  0.016645  0.006901  0.010405 -0.006363   
year               -0.000432  0.003264 -0.003731 -0.007291 -0.017351   
month              -0.007250 -0.011873 -0.005797  0.003223  0.000387   
day                 0.004271 -0.007870 -0.008482 -0.017931 -0.015605   
yearmonth          -0.004017 -0.003136 -0.006145 -0.004700 -0.014841   
target              0.151553 -0.038480 -0.015878  0.004378  0.103009   

                      amount  medical_info_a1  medical_info_a2  \
age                -0.002223        -0.003493         0.006303   
sex                 0.012535         0.005949         0.000446   
height             -0.010462         0.002690         0.005158   
weight             -0.015761         0.001887         0.026011   
product            -0.475003         0.007287         0.002404   
amount              1.000000        -0.001091        -0.018879   
medical_info_a1    -0.001091         1.000000         0.007457   
medical_info_a2    -0.018879         0.007457         1.000000   
medical_info_a3    -0.015855        -0.009929         0.003349   
medical_info_b1    -0.008645         0.010048        -0.000442   
medical_info_b2     0.010972        -0.006006        -0.007074   
medical_info_b3     0.020785        -0.004971        -0.010946   
medical_info_c1    -0.014449        -0.010648         0.008673   
medical_info_c2    -0.017795         0.005606         0.035999   
medical_keyword_1  -0.013593        -0.019804         0.003664   
medical_keyword_2  -0.009249         0.002138        -0.006321   
medical_keyword_3   0.014525        -0.006696        -0.009720   
medical_keyword_4   0.001418         0.018266        -0.003045   
medical_keyword_5  -0.012102        -0.017992         0.017359   
medical_keyword_6   0.008543        -0.008929         0.015615   
medical_keyword_7  -0.000993        -0.000949        -0.014696   
medical_keyword_8   0.009649        -0.017394        -0.001761   
medical_keyword_9  -0.001270        -0.009012        -0.012565   
medical_keyword_10 -0.003916        -0.007391        -0.021421   
year               -0.012439        -0.007299        -0.013740   
month               0.003732         0.011518        -0.013197   
day                 0.007469         0.000207        -0.000468   
yearmonth       

## Prepare model

In [9]:
import xgboost as xgb
from sklearn.metrics import log_loss
import optuna

In [29]:
#Define hyper parameter tuner with optuna
def objective(trial):
    #set tuning parameter and range
    params={
        "objective" : "binary:logistic",
        "max_depth":trial.suggest_int("max_depth", 3, 10),
        "learning_rate" : 0.1,
        "min_child_weight" : trial.suggest_uniform("min_child_weight", 0.1, 10),
        "gamma" : trial.suggest_loguniform("gamma", 1e-8, 1.0),
        "colsample_bytree" : trial.suggest_uniform("colsample_bytree", 0.6, 0.95),
        "subsample" : trial.suggest_uniform("subsample", 0.6, 0.95)
    }
    
    #prepare xgb model
    dtrain = xgb.DMatrix(tr_x[features], label=tr_y)
    dvalid = xgb.DMatrix(va_x[features], label=va_y)
    num_round = 1000 
    early_stopping_rounds = 10
    watchlist = [(dtrain, 'train'), (dvalid, 'eval')]
    
    #runing model
    model = xgb.train(params, dtrain, num_round,
                   evals=watchlist, early_stopping_rounds=early_stopping_rounds,
                  verbose_eval=0)
    
    #prediction and get score
    va_pred = model.predict(dvalid)
    score = log_loss(va_y, va_pred)
    
    #minimize score
    return score

In [37]:
# define evaluate function using xgboost
def evaluate(features):
    #set hp tuner
    study = optuna.create_study(direction="minimize")
    study.optimize(objective, n_trials=40)
    #add best params to basic params
    best_params = study.best_params
    params_eva = {'objective': 'binary:logistic', 'learning_rate' : 0.1, 'silent': 1, 'random_state': 71}  #if you want to use regression and square error, you should chose objective:"reg:squarederror"
    params_eva.update(best_params)
    
    dtrain = xgb.DMatrix(tr_x[features], label=tr_y)
    dvalid = xgb.DMatrix(va_x[features], label=va_y)
 
    num_round = 1000 
    early_stopping_rounds = 10
    watchlist = [(dtrain, 'train'), (dvalid, 'eval')]
    model = xgb.train(params_eva, dtrain, num_round,
                      evals=watchlist, early_stopping_rounds=early_stopping_rounds,
                      verbose_eval=0)
    va_pred = model.predict(dvalid)
    score = log_loss(va_y, va_pred)

    return score

## Greedy Forward Selection

In [38]:
best_score = 9999.0
selected = set([])

print('start greedy forward selection')

while True:

    if len(selected) == len(train_x.columns):
        # all features selected and end
        break

    scores = []
    for feature in train_x.columns:
        if feature not in selected:
            fs = list(selected) + [feature]
            score = evaluate(fs)
            scores.append((feature, score))

    # minimum score is the best in this example. If you use other scoring index, you need rewrite below.
    b_feature, b_score = sorted(scores, key=lambda tpl: tpl[1])[0]
    if b_score < best_score:
        selected.add(b_feature)
        best_score = b_score
        print(f'selected:{b_feature}')
        print(f'score:{b_score}')
    else:
        # we can't improve score any more, so finish
        break

print(f'selected features: {selected}')

start greedy forward selection


/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:24,725] Finished trial#0 resulted in value: 0.2540397948138416. Current best value is 0.2540397948138416 with parameters: {'max_depth': 4, 'min_child_weight': 7.329750037321025, 'gamma': 3.753723358065166e-05, 'colsample_bytree': 0.9342448363356989, 'subsample': 0.779142576020535}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:25,401] Finished trial#1 resulted in value: 0.2292723783143796. Current best value is 0.2292723783143796 with parameters: {'max_depth': 7, 'min_child_weight': 5.078441582406588, 'gamma': 5.648451831045488e-08, 'colsample_bytree': 0.6891407892511563, 'subsample': 0.7984522957667748}.
/Users/hasegawatooru/anaconda3/envs/kaggle/

[I 2019-12-26 22:15:34,329] Finished trial#17 resulted in value: 0.2161292730868212. Current best value is 0.2161292730868212 with parameters: {'max_depth': 8, 'min_child_weight': 4.36134261771296, 'gamma': 3.740973424541988e-06, 'colsample_bytree': 0.8735908747047275, 'subsample': 0.7403941987351133}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:34,624] Finished trial#18 resulted in value: 0.29172916964516044. Current best value is 0.2161292730868212 with parameters: {'max_depth': 8, 'min_child_weight': 4.36134261771296, 'gamma': 3.740973424541988e-06, 'colsample_bytree': 0.8735908747047275, 'subsample': 0.7403941987351133}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:35,340] Finished tria

[I 2019-12-26 22:15:45,796] Finished trial#34 resulted in value: 0.22533876886535437. Current best value is 0.2161292730868212 with parameters: {'max_depth': 8, 'min_child_weight': 4.36134261771296, 'gamma': 3.740973424541988e-06, 'colsample_bytree': 0.8735908747047275, 'subsample': 0.7403941987351133}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:46,279] Finished trial#35 resulted in value: 0.2487469830552116. Current best value is 0.2161292730868212 with parameters: {'max_depth': 8, 'min_child_weight': 4.36134261771296, 'gamma': 3.740973424541988e-06, 'colsample_bytree': 0.8735908747047275, 'subsample': 0.7403941987351133}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:46,805] Finished tria

[I 2019-12-26 22:15:56,062] Finished trial#11 resulted in value: 0.2269224195799092. Current best value is 0.21933791888240375 with parameters: {'max_depth': 10, 'min_child_weight': 3.4782064691201318, 'gamma': 0.0008164683377184293, 'colsample_bytree': 0.7135474543184194, 'subsample': 0.6734163568924665}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:56,677] Finished trial#12 resulted in value: 0.234654639167618. Current best value is 0.21933791888240375 with parameters: {'max_depth': 10, 'min_child_weight': 3.4782064691201318, 'gamma': 0.0008164683377184293, 'colsample_bytree': 0.7135474543184194, 'subsample': 0.6734163568924665}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 22:15:57,305] Finishe

...

[I 2019-12-27 00:26:22,938] Finished trial#19 resulted in value: 0.22723408329184167. Current best value is 0.21670299325456727 with parameters: {'max_depth': 10, 'min_child_weight': 9.773806098098566, 'gamma': 0.033123718388144936, 'colsample_bytree': 0.8808903593184527, 'subsample': 0.899980647678002}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:23,297] Finished trial#20 resulted in value: 0.264375054140389. Current best value is 0.21670299325456727 with parameters: {'max_depth': 10, 'min_child_weight': 9.773806098098566, 'gamma': 0.033123718388144936, 'colsample_bytree': 0.8808903593184527, 'subsample': 0.899980647678002}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:23,736] Finished tri

[I 2019-12-27 00:26:34,362] Finished trial#36 resulted in value: 0.25963963658809663. Current best value is 0.21561065042632982 with parameters: {'max_depth': 8, 'min_child_weight': 2.640225182317586, 'gamma': 0.0002784075209506908, 'colsample_bytree': 0.7796596316210243, 'subsample': 0.8429966309758338}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:35,181] Finished trial#37 resulted in value: 0.22409103308303746. Current best value is 0.21561065042632982 with parameters: {'max_depth': 8, 'min_child_weight': 2.640225182317586, 'gamma': 0.0002784075209506908, 'colsample_bytree': 0.7796596316210243, 'subsample': 0.8429966309758338}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:35,327] Finished

[I 2019-12-27 00:26:43,963] Finished trial#13 resulted in value: 0.2393961942674592. Current best value is 0.21805917685392778 with parameters: {'max_depth': 6, 'min_child_weight': 0.20766344506271806, 'gamma': 1.95609468285915e-08, 'colsample_bytree': 0.637622378480018, 'subsample': 0.9045692621583211}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:44,536] Finished trial#14 resulted in value: 0.23757441450441255. Current best value is 0.21805917685392778 with parameters: {'max_depth': 6, 'min_child_weight': 0.20766344506271806, 'gamma': 1.95609468285915e-08, 'colsample_bytree': 0.637622378480018, 'subsample': 0.9045692621583211}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:45,164] Finished 

[I 2019-12-27 00:26:53,356] Finished trial#30 resulted in value: 0.21698568733863066. Current best value is 0.21054958698193077 with parameters: {'max_depth': 7, 'min_child_weight': 4.0097120460851485, 'gamma': 6.884898581192933e-08, 'colsample_bytree': 0.7683238309178487, 'subsample': 0.8903003151592908}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:54,114] Finished trial#31 resulted in value: 0.22034342960387002. Current best value is 0.21054958698193077 with parameters: {'max_depth': 7, 'min_child_weight': 4.0097120460851485, 'gamma': 6.884898581192933e-08, 'colsample_bytree': 0.7683238309178487, 'subsample': 0.8903003151592908}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-27 00:26:54,765] Finish

selected features: {'medical_keyword_2', 'medical_info_c2', 'medical_keyword_1', 'product', 'medical_info_b1', 'weight', 'medical_keyword_5', 'age', 'medical_info_a2', 'height', 'medical_keyword_4', 'medical_keyword_3', 'medical_info_a3', 'medical_info_a1', 'medical_info_c1'}


In [39]:
print(selected, len(selected))
#after feature selection reduce 13 features.

{'medical_keyword_2', 'medical_info_c2', 'medical_keyword_1', 'product', 'medical_info_b1', 'weight', 'medical_keyword_5', 'age', 'medical_info_a2', 'height', 'medical_keyword_4', 'medical_keyword_3', 'medical_info_a3', 'medical_info_a1', 'medical_info_c1'} 15


## Abstract of this package in Japanese lite version  
上記のGreedy forward selectionは特徴量が増えると計算量が特徴量の数の２乗に比例する。単純化し、軽くした（特徴量の数に比例）ものの手順は以下。  
1. 使用する特徴量の集合を空から始める（この集合をMとする）  
2. 特徴量の候補を有望な順ｏｒランダムに並べる  
3. 次の特徴量を加えてスコア（評価指標）が改善すればMに加える（そうならない場合は加えない。このときハイパーパラメータのチューニングもする）  
4. ３をすべての候補について繰り返す　　  

In [23]:
best_score = 9999.0
candidates = np.random.RandomState(71).permutation(train_x.columns)
selected = set([])

print('start simple selection')
for feature in candidates:
    fs = list(selected) + [feature]
    score = evaluate(fs)

    if score < best_score:
        selected.add(feature)
        best_score = score
        print(f'selected:{feature}')
        print(f'score:{score}')

print(f'selected features: {selected}')

start simple selection


/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 20:59:30,415] Finished trial#0 resulted in value: 0.221938235707744. Current best value is 0.221938235707744 with parameters: {'max_depth': 8, 'min_child_weight': 8.06068045613747, 'gamma': 6.684373682126317e-05, 'colsample_bytree': 0.6171989461760875, 'subsample': 0.6942542738210808}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 20:59:31,372] Finished trial#1 resulted in value: 0.22707980071075726. Current best value is 0.221938235707744 with parameters: {'max_depth': 8, 'min_child_weight': 8.06068045613747, 'gamma': 6.684373682126317e-05, 'colsample_bytree': 0.6171989461760875, 'subsample': 0.6942542738210808}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib

[I 2019-12-26 20:59:45,736] Finished trial#17 resulted in value: 0.23303679952640086. Current best value is 0.21358965721203713 with parameters: {'max_depth': 9, 'min_child_weight': 7.467092540206121, 'gamma': 1.1171768199079289e-07, 'colsample_bytree': 0.6681023397926383, 'subsample': 0.9494155031460939}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 20:59:46,458] Finished trial#18 resulted in value: 0.22729363270378672. Current best value is 0.21358965721203713 with parameters: {'max_depth': 9, 'min_child_weight': 7.467092540206121, 'gamma': 1.1171768199079289e-07, 'colsample_bytree': 0.6681023397926383, 'subsample': 0.9494155031460939}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 20:59:46,930] Finish

[I 2019-12-26 20:59:59,483] Finished trial#34 resulted in value: 0.2433492823285982. Current best value is 0.21358965721203713 with parameters: {'max_depth': 9, 'min_child_weight': 7.467092540206121, 'gamma': 1.1171768199079289e-07, 'colsample_bytree': 0.6681023397926383, 'subsample': 0.9494155031460939}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:00:00,076] Finished trial#35 resulted in value: 0.2564715682540089. Current best value is 0.21358965721203713 with parameters: {'max_depth': 9, 'min_child_weight': 7.467092540206121, 'gamma': 1.1171768199079289e-07, 'colsample_bytree': 0.6681023397926383, 'subsample': 0.9494155031460939}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:00:01,162] Finished

selected:product
score:0.48572545695900915


...

[I 2019-12-26 21:10:59,819] Finished trial#28 resulted in value: 0.24696951864799485. Current best value is 0.21600991616483078 with parameters: {'max_depth': 9, 'min_child_weight': 8.70489143957873, 'gamma': 0.09884408178759908, 'colsample_bytree': 0.6260357638664762, 'subsample': 0.8064136685190118}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:11:00,471] Finished trial#29 resulted in value: 0.22712781416985672. Current best value is 0.21600991616483078 with parameters: {'max_depth': 9, 'min_child_weight': 8.70489143957873, 'gamma': 0.09884408178759908, 'colsample_bytree': 0.6260357638664762, 'subsample': 0.8064136685190118}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:11:01,088] Finished trial

[I 2019-12-26 21:11:11,010] Finished trial#5 resulted in value: 0.26080902282483875. Current best value is 0.2161094260335667 with parameters: {'max_depth': 6, 'min_child_weight': 8.64107467644324, 'gamma': 0.051102477485478956, 'colsample_bytree': 0.663434354975486, 'subsample': 0.8050245007929961}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:11:11,502] Finished trial#6 resulted in value: 0.23399827255308628. Current best value is 0.2161094260335667 with parameters: {'max_depth': 6, 'min_child_weight': 8.64107467644324, 'gamma': 0.051102477485478956, 'colsample_bytree': 0.663434354975486, 'subsample': 0.8050245007929961}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:11:12,693] Finished trial#7 r

[I 2019-12-26 21:11:23,344] Finished trial#22 resulted in value: 0.2518709913957864. Current best value is 0.21272362741087564 with parameters: {'max_depth': 7, 'min_child_weight': 5.178573962509519, 'gamma': 1.5093340540434616e-08, 'colsample_bytree': 0.8727510339296428, 'subsample': 0.8184220888513002}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:11:23,851] Finished trial#23 resulted in value: 0.23995763300377876. Current best value is 0.21272362741087564 with parameters: {'max_depth': 7, 'min_child_weight': 5.178573962509519, 'gamma': 1.5093340540434616e-08, 'colsample_bytree': 0.8727510339296428, 'subsample': 0.8184220888513002}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version

[I 2019-12-26 21:11:24,444] Finishe

[I 2019-12-26 21:11:33,878] Finished trial#39 resulted in value: 0.23563501722617075. Current best value is 0.20300702260088874 with parameters: {'max_depth': 5, 'min_child_weight': 6.484455623824589, 'gamma': 1.152459969428792e-08, 'colsample_bytree': 0.8313003361984355, 'subsample': 0.8327973690828486}.
/Users/hasegawatooru/anaconda3/envs/kaggle/lib/python3.6/site-packages/xgboost/core.py:587: FutureWarning:

Series.base is deprecated and will be removed in a future version



selected features: {'medical_info_b2', 'medical_keyword_2', 'medical_keyword_10', 'product', 'amount', 'month', 'medical_info_a3', 'weight', 'sex', 'medical_keyword_5', 'medical_info_a2', 'age', 'height', 'medical_keyword_4', 'medical_keyword_3', 'medical_keyword_9', 'medical_info_a1', 'medical_info_c1'}


In [24]:
print(selected, len(selected))
#after feature selection reduce 10 features.

{'medical_info_b2', 'medical_keyword_2', 'medical_keyword_10', 'product', 'amount', 'month', 'medical_info_a3', 'weight', 'sex', 'medical_keyword_5', 'medical_info_a2', 'age', 'height', 'medical_keyword_4', 'medical_keyword_3', 'medical_keyword_9', 'medical_info_a1', 'medical_info_c1'} 18
